<a href="https://colab.research.google.com/github/yashveersinghsohi/machine_hack_competitions/blob/eda/Data_Science_Student_Championship/Competition_Files/Solution_notebook.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
# !git clone -b eda https://github.com/yashveersinghsohi/machine_hack_competitions.git

In [ ]:
# !pip install ipykernel
# !pip install --upgrade nbformat

In [3]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px
import pandas as pd
import numpy as np
from xgboost import XGBRFRegressor
from sklearn.metrics import mean_squared_log_error
from sklearn.model_selection import train_test_split

In [6]:
# Load the data
root_dir = '/content/machine_hack_competitions/Data_Science_Student_Championship/Competition_Files/'
train = pd.read_csv(root_dir+"train.csv")
test = pd.read_csv(root_dir+"test.csv")
submission = pd.read_csv(root_dir+"submission.csv")

In [7]:
train

trip_duration  distance_traveled  num_of_passengers    fare  tip  \
0               748.0               2.75                1.0   75.00   24   
1              1187.0               3.43                1.0  105.00   24   
2               730.0               3.12                1.0   71.25    0   
3               671.0               5.63                3.0   90.00    0   
4               329.0               2.09                1.0   45.00   12   
...               ...                ...                ...     ...  ...   
209668         1617.0               8.42                1.0  150.00   47   
209669          438.0               1.29                1.0   48.75   12   
209670          571.0               2.82                1.0   63.75    0   
209671          491.0               2.16                1.0   56.25    0   
209672         3614.0              33.72                1.0  337.50    0   

        miscellaneous_fees  total_fare  surge_applied  
0                    6.300     105.300              0  
1                   13.200     142.200              0  
2                   26.625      97.875              1  
3                    9.750      99.750              0  
4                   13.200      70.200              0  
...                    ...         ...            ...  
209668               5.800     202.800              0  
209669              34.575      95.325              1  
209670               6.000      69.750              0  
209671              13.500      69.750              0  
209672               2.250     339.750              0  

[209673 rows x 8 columns]

In [8]:
test

trip_duration  distance_traveled  num_of_passengers  fare  tip  \
0             1076.0               4.18                1.0     0    0   
1              429.0               1.48                4.0     0    0   
2              856.0               4.15                1.0     0   24   
3              622.0               3.22                1.0     0   15   
4              507.0               3.98                1.0     0    0   
...              ...                ...                ...   ...  ...   
89856          435.0               2.24                1.0     0   13   
89857          519.0               2.61                1.0     0    7   
89858          450.0               2.24                1.0     0    0   
89859          919.0               4.12                1.0     0   25   
89860          441.0               3.52                1.0     0   23   

       miscellaneous_fees  total_fare  surge_applied  
0                  13.500           0              0  
1                  13.500           0              0  
2                   6.000           0              0  
3                   5.625           0              0  
4                   2.250           0              0  
...                   ...         ...            ...  
89856              13.700           0              0  
89857              13.850           0              0  
89858              26.625           0              1  
89859              30.200           0              1  
89860               6.175           0              0  

[89861 rows x 8 columns]

In [9]:
submission

total_fare
0             0.0
1             0.0
2             0.0
3             0.0
4             0.0
...           ...
89856         0.0
89857         0.0
89858         0.0
89859         0.0
89860         0.0

[89861 rows x 1 columns]

In [10]:
train.shape

(209673, 8)

In [11]:
test.shape

(89861, 8)

In [12]:
# This code checks the type of the train variable
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 209673 entries, 0 to 209672
Data columns (total 8 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   trip_duration       209673 non-null  float64
 1   distance_traveled   209673 non-null  float64
 2   num_of_passengers   209673 non-null  float64
 3   fare                209673 non-null  float64
 4   tip                 209673 non-null  int64  
 5   miscellaneous_fees  209673 non-null  float64
 6   total_fare          209673 non-null  float64
 7   surge_applied       209673 non-null  int64  
dtypes: float64(6), int64(2)
memory usage: 12.8 MB


In [13]:
# This code prints the information about the test dataframe
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 89861 entries, 0 to 89860
Data columns (total 8 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   trip_duration       89861 non-null  float64
 1   distance_traveled   89861 non-null  float64
 2   num_of_passengers   89861 non-null  float64
 3   fare                89861 non-null  int64  
 4   tip                 89861 non-null  int64  
 5   miscellaneous_fees  89861 non-null  float64
 6   total_fare          89861 non-null  int64  
 7   surge_applied       89861 non-null  int64  
dtypes: float64(4), int64(4)
memory usage: 5.5 MB


In [14]:
# This code describes the training data
train.describe()

trip_duration  distance_traveled  num_of_passengers           fare  \
count  209673.000000      209673.000000      209673.000000  209673.000000   
mean     1173.181478           5.054431           1.292808      99.623431   
std      4775.653621         125.217419           0.930754      85.602702   
min         0.000000           0.020000           0.000000       0.000000   
25%       446.000000           1.950000           1.000000      52.500000   
50%       707.000000           3.200000           1.000000      75.000000   
75%      1098.000000           5.730000           1.000000     116.250000   
max     86387.000000       57283.910000           9.000000    4466.250000   

                 tip  miscellaneous_fees     total_fare  surge_applied  
count  209673.000000       209673.000000  209673.000000  209673.000000  
mean       13.030824           15.136829     127.791084       0.280523  
std        20.367764           12.553436      98.797374       0.449256  
min         0.000000           -0.500000       0.000000       0.000000  
25%         0.000000            6.000000      70.200000       0.000000  
50%         9.000000            9.750000     101.700000       0.000000  
75%        20.000000           26.450000     152.250000       1.000000  
max      2500.000000          435.000000    4472.250000       1.000000

In [15]:
# describe the test

test.describe()

trip_duration  distance_traveled  num_of_passengers     fare  \
count   89861.000000       89861.000000       89861.000000  89861.0   
mean     1148.178164           7.263529           1.286732      0.0   
std      4611.480867         554.965869           0.920910      0.0   
min         0.000000           0.020000           0.000000      0.0   
25%       446.000000           1.950000           1.000000      0.0   
50%       705.000000           3.200000           1.000000      0.0   
75%      1094.000000           5.730000           1.000000      0.0   
max     86395.000000      145517.600000           9.000000      0.0   

                tip  miscellaneous_fees  total_fare  surge_applied  
count  89861.000000        89861.000000     89861.0   89861.000000  
mean      13.031048           15.190636         0.0       0.282280  
std       18.692751           12.677904         0.0       0.450112  
min        0.000000           -0.500000         0.0       0.000000  
25%        0.000000            6.000000         0.0       0.000000  
50%        9.000000            9.750000         0.0       0.000000  
75%       20.000000           26.450000         0.0       1.000000  
max      719.000000          431.500000         0.0       1.000000

In [16]:
# This code creates a scatter plot of the trip duration and the distance traveled.
# It uses the Plotly Express library to create the plot.
# The plot shows that there is a positive correlation between trip duration and distance traveled.

fig = px.scatter(train, x="trip_duration", y="distance_traveled")
fig.show()

In [19]:
# This code creates a scatter plot of the trip duration and fare
fig = px.scatter(train, x="trip_duration", y="fare")
fig.show()

In [17]:
# This code generates a scatter plot of the number of passengers and the fare.

fig = px.scatter(train, x="num_of_passengers", y="fare")
fig.show()

In [18]:
# A comment explaining what this code does

fig = px.pie(train, values="tip", names="num_of_passengers")
fig.show()

In [20]:
# This code calculates the correlation between the trip duration and the distance traveled.
train["trip_duration"].corr(train["distance_traveled"])

0.005773932457209867

In [21]:
# This code creates a scatter plot of trip duration vs. distance traveled
fig = px.scatter(test, x="trip_duration", y="distance_traveled")
fig.show()

In [22]:
# This code finds the correlation between trip duration and distance traveled.
# The code uses the trip_duration and distance_traveled columns from the test dataset.

test["trip_duration"].corr(test["distance_traveled"])

0.002006326641157824

In [24]:
# Load the training data
train_df = pd.read_csv(root_dir+'train.csv')

# Separate the features and the target variable for fare prediction
features = ['trip_duration', 'distance_traveled', 'num_of_passengers', 'surge_applied']
target = 'fare'

X = train_df[features]
y = train_df[target]

In [25]:
# Split the data into training set and validation set
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.1, random_state=42)

# Define the model
model_fare = XGBRFRegressor()

# Train the model
model_fare.fit(X_train, y_train)

# Predict the validation set results
y_pred_val = model_fare.predict(X_val)

In [26]:
# Calculate the RMSLE
rmsle = np.sqrt(mean_squared_log_error(y_val, y_pred_val))
print(f"Validation RMSLE: {rmsle}")

Validation RMSLE: 0.25056175101801775


In [28]:
# Now load the test data
test_df = pd.read_csv(root_dir+'test.csv')

# Predict the fare in the test set
test_df['fare'] = model_fare.predict(test_df[features])

# Now let's calculate total fare = fare + tip + miscellaneous_fees
test_df['total_fare'] = test_df['fare'] + test_df['tip'] + test_df['miscellaneous_fees']

# Save the test dataframe with the predictions for the final sample submission
test_df['total_fare'].to_csv('submission.csv', index=False)